In [21]:
import pandas as pd
import regex as re
from collections import Counter
import emoji
from gensim.models.word2vec import Word2Vec
import nltk
from nltk import word_tokenize
from gensim.models import FastText
from gensim.models import KeyedVectors
#from nltk.tokenize import word_tokenize
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
import numpy as np
#from tqdm import tqdm
from gensim.models.callbacks import CallbackAny2Vec
#import matplotlib.pyplot as plt
import keras
from keras.preprocessing.text import Tokenizer
from keras.utils.data_utils import pad_sequences
#from keras.initializers import Constant
from keras.layers import ReLU
from keras.layers import Dropout
from keras.models import Sequential
from keras.layers import Dense, Flatten, Embedding, Input, LSTM, Bidirectional, TimeDistributed, Conv1D, MaxPooling1D, GlobalMaxPooling1D
from keras.optimizers import Adam
from keras import Model
from keras.models import load_model
from keras.callbacks import EarlyStopping
from tensorflow.keras.utils import to_categorical
import math
nltk.download('punkt')

[nltk_data] Downloading package punkt to /home/user/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [22]:
df_hing_eng = pd.read_pickle('dataset/hinglish_english_tweet_ids_data.pkl')
#print(df_hing_eng.columns)
#print(df_hing_eng[['tweet_text']])
#df_hing_eng = df_hing_eng['tweet_text']
df_hing_eng = df_hing_eng[['tweet_text']].copy()
print(len(df_hing_eng))
print(df_hing_eng.columns)

422415
Index(['tweet_text'], dtype='object')


In [23]:
#finds the duplicate rows in the unlabeled Hinglish-English data

duplicate_1 = df_hing_eng[df_hing_eng.duplicated(keep='first')]
print(len(duplicate_1))
print(duplicate_1)
#print(type(duplicate_1))

17695
                                               tweet_text
368     Chitti ai hai ai hai chitthi ai hai = I have m...
372     Chitti ai hai ai hai chitthi ai hai = I have m...
393                    Kim Kardashian is virgin. #sarcasm
394                    Kim Kardashian is virgin. #sarcasm
423                    Kim Kardashian is virgin. #sarcasm
...                                                   ...
422093                                                 hi
422100                                   is going to bed.
422121                                             nothin
422141                                           wakes up
422251                                      in the office

[17695 rows x 1 columns]


In [24]:
#removes duplicates

df_hing_eng = df_hing_eng.drop_duplicates(keep='first')
print(len(df_hing_eng))

duplicate_2 = df_hing_eng[df_hing_eng.duplicated(keep='first')]
print(len(duplicate_2))
print(df_hing_eng.columns)

404720
0
Index(['tweet_text'], dtype='object')


In [25]:
df_labeled = pd.read_pickle('dataset/data_soumyadeep.pkl')
df_labeled = df_labeled[['tweet_text', 'is_sarcastic']].copy()
print(len(df_labeled))
print(df_labeled.columns)

94788
Index(['tweet_text', 'is_sarcastic'], dtype='object')


In [26]:
#finds the duplicate rows in the labeled data

duplicate_3 = df_labeled[df_labeled.duplicated(subset=['tweet_text'], keep='first')]
print(len(duplicate_3))
print(duplicate_3)

2895
                                              tweet_text  is_sarcastic
354    RT Apna vyauhar hoga aise jal mein kamal rehat...             0
630    @fittaymunhapka n osky baad amMi ny kha k kuch...             0
686    RT Teen behan ke baad jo aata putra woh trekha...             0
809    Ek aadmi pareshan ho kar Ae bhagwan aisi zinda...             1
844    RT Teen behan ke baad jo aata putra woh trekha...             0
...                                                  ...           ...
94716  RT Teen behan ke baad jo aata putra woh trekha...             0
94721  Roz badh'taa huun jahaa'n se aage // Phir wahi...             0
94747  RT Chhoota vaibhav schooli shiksha shooro ho g...             0
94756                                kya hoga is desh ka             0
94763  @rjauhari lol  unka bhi mast hoga..koi recessi...             0

[2895 rows x 2 columns]


In [27]:
#removes duplicates from labeled data

df_labeled = df_labeled.drop_duplicates(subset=['tweet_text'], keep='first')
print(len(df_labeled))

duplicate_4 = df_labeled[df_labeled.duplicated(keep='first')]
print(len(duplicate_4))
print(df_labeled.columns)

91893
0
Index(['tweet_text', 'is_sarcastic'], dtype='object')


In [28]:
#finds the common rows between unlabeled Hinglish English embedding data and labeled data

common_rows = pd.merge(df_hing_eng, df_labeled, how = 'inner', on=['tweet_text'])
print(common_rows)
len(common_rows)
#print(type(common_rows))

                                              tweet_text  is_sarcastic
0      @ajuonline #sarcasm Haal chaal thik thak hai-s...             1
1               @I_Am_Hollywood - Charlie Haas? #sarcasm             1
2                       Chetan Bhagat #epicmale #sarcasm             1
3      @Bo_jasim86 LOOL 7atheer affaa 3allaik rgoobti...             1
4      @FENUSF tees2al 3anek el 3afiaa 7abeeb galbe ,...             1
...                                                  ...           ...
54025   BHAI NEEND HEE NI ARAHI AKHIR KIA MAZAK HAI??)??             1
54026  - Neend Toh Bachpan Mein Aaya Karti Thi..!! - ...             1
54027  aik larki late night neend se jagi aur.. fb pe...             1
54028  @FarahKhanAli really funny.. lagta hai.... sub...             1
54029  @Rudeicious ab tum meri neend ka aise Mazak ur...             1

[54030 rows x 2 columns]


54030

In [29]:
#removes all the common rows from unlabeled data

#cond = df1['Email'].isin(df2['Email'])
#df1.drop(df1[cond].index, inplace = True)

common = df_hing_eng['tweet_text'].isin(df_labeled['tweet_text'])
df_hing_eng.drop(df_hing_eng[common].index, inplace=True)
print(len(df_hing_eng))
print(df_hing_eng.columns)

common_rows2 = pd.merge(df_hing_eng, df_labeled, how = 'inner', on=['tweet_text'])
#print(common_rows2)
print(len(common_rows2))

350690
Index(['tweet_text'], dtype='object')
0


In [30]:
#removes all rows from the Dataframe containing Devanagari script (any non-English word) 

df_hing_eng = df_hing_eng[df_hing_eng['tweet_text'].map(lambda x: x.isascii())]
print(len(df_hing_eng))

318723


In [31]:
#removes mentions, '#', emojis, punctuations, special chars, URLs, words containing numbers, spaces from beginning and end of tweets

def data_preprocessing(source):
    
    source = source.str.lower() #lower case chars
    source = source.str.replace("\w*\d\w*","") #removes all words containing numbers
    #source = source.str.replace("#", "")
    #source = source.str.replace("@", "")
    #source = source.str.replace("@[A-Za-z0-9_]+","")
    source = source.str.replace("[@A-Za-z0-9_]*@[@A-Za-z0-9_]*","")
    #source = source.str.replace("#[A-Za-z0-9_]+","")
    source = source.str.replace("[#A-Za-z0-9_]*#[#A-Za-z0-9_]*","")
    source = source.str.replace("\s+|[!$%&()*+, -./:;<=>?\^_`{|}~]\s*"," ")
    source = source.str.replace("http\S+","")
    
    return source

df_hing_eng['tweet_text'] = data_preprocessing(df_hing_eng['tweet_text'])
df_hing_eng['tweet_text'] = df_hing_eng['tweet_text'].apply(lambda s: emoji.replace_emoji(s,""))
df_hing_eng['tweet_text'] = df_hing_eng['tweet_text'].str.strip()
df_hing_eng.head()

/tmp/ipykernel_3873/2924867879.py:6: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("\w*\d\w*","") #removes all words containing numbers
/tmp/ipykernel_3873/2924867879.py:10: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("[@A-Za-z0-9_]*@[@A-Za-z0-9_]*","")
/tmp/ipykernel_3873/2924867879.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("[#A-Za-z0-9_]*#[#A-Za-z0-9_]*","")
/tmp/ipykernel_3873/2924867879.py:13: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("\s+|[!$%&()*+, -./:;<=>?\^_`{|}~]\s*"," ")
/tmp/ipykernel_3873/2924867879.py:14: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("http\S+","")


tweet_text
167                                      dary emratiba
194  yograj singh  dhoni advised dd management to r...
200  seedhe log hai ma beta ab  crore ka ghotala ho...
309  ab ham khade ho gaye hain   ab ham aur bhi dar...
470                                    make up hayoona

In [32]:
#finds the unique words in the unlabeled data

unique_words = set()
df_hing_eng['tweet_text'].str.lower().str.split().apply(unique_words.update)
unique_words = list(unique_words)
#print(unique_words)
#print('---------------')
print(len(unique_words))

197446


In [33]:
#counts the appearances of the words in the unlabeled data

results = Counter()
df_hing_eng['tweet_text'].str.lower().str.split().apply(results.update)
print(results)
#print('-----------------')
#print(type(results))
#print('-----------------')

Counter({'hai': 152652, 'to': 71666, 'ki': 70307, 'ko': 61566, 'se': 60483, 'ho': 50264, 'ke': 49419, 'ka': 48442, 'nahi': 47411, 'bhi': 46218, 'k': 43403, 'me': 36236, 'aur': 35370, 'na': 33655, 'hi': 29056, 'kya': 28926, 'hain': 28917, 'kar': 27119, 'mein': 26934, 'koi': 24270, 'ye': 23679, 'ek': 21644, 'the': 20977, 'main': 20872, 'jo': 19974, 'tha': 19776, 'aap': 19569, 'tum': 18752, 'http': 18361, 'ne': 18286, 'kuch': 17691, 'hum': 17394, 'bhai': 17086, 'raha': 16697, 'is': 15904, 'wo': 15854, 'hota': 15547, 'a': 15331, 'par': 15246, 'ab': 14818, 'liye': 14801, 'kabhi': 14794, 'gaya': 14736, 'mai': 14402, 'tu': 14300, 'he': 13495, 'i': 13381, 'phir': 12748, 'din': 12359, 'agar': 11997, 'in': 11987, 'toh': 11523, 'or': 11474, 'baat': 11435, 'aaj': 11410, 'jab': 11293, 'pe': 10918, 'mujhe': 10890, 'tere': 10884, 'h': 10859, 'dil': 10846, 'mera': 10763, 'sirf': 10711, 'raat': 10528, 'e': 10485, 'mere': 10454, 'karne': 10407, 'lekin': 10312, 'apna': 10283, 'p': 10204, 'kisi': 10018, '

In [34]:
#finds the rare words in the unlabeled data

rare_words_unlabeled = []
for item in results:
    if results[item]<10:
       #print(item, results[item])
       rare_words_unlabeled.append(item)
        
print(rare_words_unlabeled)  
print('-----------------------')
print(len(rare_words_unlabeled))
print('-----------------------')

with open("rare_words_hing_eng.txt", "w") as file:
    file.write(str(rare_words_unlabeled))

['dary', 'emratiba', 'yograj', 'advised', 'daraayenge', 'hayoona', 'seekhay', 'insey', 'buta', 'vaio', 'aanaayi', 'janichirunengil', 'kashtapettu', 'undakki', 'okke', 'vangendi', 'vannene', 'bhagyam', 'pennayond', 'athu', 'vendallo', 'insanoo', 'casts', 'hypocrisy', 'underrated', 'phatake', 'batayain', 'aasoo', 'gracy', 'dilwado', 'qadhafi', 'hails', 'vstz', 'kalavati', 'austerity', 'resident', 'nominated', 'mehsud', 'hflv', 'rehabilitation', 'tamils', 'bimal', 'celebrates', 'toop', 'basiji', 'nadarad', 'virginity', 'admitted', 'gopalkrishna', 'greets', 'welfare', 'rameshwar', 'pokhriyal', 'winds', 'greet', 'shivshankar', 'menon', 'koshiyari', 'quits', 'sarvajan', 'bahujan', 'ideological', 'bind', 'congratulated', 'berths', 'nil', 'retain', 'kannauj', 'buddhadeb', 'tulf', 'aiyar', 'fails', 'mayiladuthurai', 'loses', 'jangipur', 'vijayashanti', 'patnaik', 'hinjili', 'maneka', 'janardhana', 'poojary', 'defeated', 'dakshina', 'trails', 'firozabad', 'qbfzus', 'dikshit', 'ensure', 'jayalali

In [35]:
with open("rare_words_hing_eng.txt", "r") as file:
    rare_words_unlabeled = eval(file.readline())

#print(rare_words, type(rare_words), type(rare_words[0]))

In [18]:
#--->don't run it now
#removes rare words from the unlabeled data

df_hing_eng['tweet_text'] = df_hing_eng['tweet_text'].apply(lambda x: ' '.join([word for word in x.split() if word not in (rare_words_unlabeled)]))
print(df_hing_eng.head())

                                            tweet_text
167                                                   
194      singh dhoni dd management to release yuvraj p
200  seedhe log hai ma beta ab crore ka ghotala ho ...
309           ab ham khade ho gaye hain ab ham aur bhi
470                                            make up


In [19]:
#--->don't run it now
#saves the preprocessed dataframe to a pickle file

print(df_hing_eng[['tweet_text']].head())
df_hing_eng.to_pickle('preprocessed_hing_eng.pkl')

                                            tweet_text
167                                                   
194      singh dhoni dd management to release yuvraj p
200  seedhe log hai ma beta ab crore ka ghotala ho ...
309           ab ham khade ho gaye hain ab ham aur bhi
470                                            make up


In [36]:
#loads the preprocessed dataframe from a pickle file

df_hing_eng = pd.read_pickle('preprocessed_hing_eng.pkl')
#print(df[['tweet_text']].head(5))
print(df_hing_eng.head())

                                            tweet_text
167                                                   
194      singh dhoni dd management to release yuvraj p
200  seedhe log hai ma beta ab crore ka ghotala ho ...
309           ab ham khade ho gaye hain ab ham aur bhi
470                                            make up


In [37]:
#finds the unique words in the unlabeled data after rare words removal

unique_words = set()
df_hing_eng['tweet_text'].str.lower().str.split().apply(unique_words.update)
unique_words = list(unique_words)
#print(unique_words)
#print('---------------')
print(len(unique_words))

24379


In [38]:
#generates tokenized data for the preprocessed data

#nltk.download('punkt')
df_hing_eng['tweet_text'] = df_hing_eng['tweet_text'].apply(nltk.word_tokenize)
df_hing_eng.head(10)

tweet_text
167                                                  []
194   [singh, dhoni, dd, management, to, release, yu...
200   [seedhe, log, hai, ma, beta, ab, crore, ka, gh...
309   [ab, ham, khade, ho, gaye, hain, ab, ham, aur,...
470                                          [make, up]
571             [cut, marna, koi, umar, se, nahi, haha]
804   [woh, jo, kar, rahe, haen, woh, desh, sewa, ha...
905   [u, r, aapne, chaata, nahi, ki, tarah, pehle, ...
1077               [bhai, tu, ek, mini, laptop, le, le]
1277                                       [cash, flat]

In [39]:
#removes all the rows with empty lists

df_hing_eng=df_hing_eng[df_hing_eng['tweet_text'].map(lambda d: len(d)) > 0]
df_hing_eng.head(10)

tweet_text
194   [singh, dhoni, dd, management, to, release, yu...
200   [seedhe, log, hai, ma, beta, ab, crore, ka, gh...
309   [ab, ham, khade, ho, gaye, hain, ab, ham, aur,...
470                                          [make, up]
571             [cut, marna, koi, umar, se, nahi, haha]
804   [woh, jo, kar, rahe, haen, woh, desh, sewa, ha...
905   [u, r, aapne, chaata, nahi, ki, tarah, pehle, ...
1077               [bhai, tu, ek, mini, laptop, le, le]
1277                                       [cash, flat]
1381  [mere, bulane, se, koi, aata, hi, nhi, sab, bo...

In [40]:
model = Word2Vec(df_hing_eng['tweet_text'], vector_size=300, window=10, hs=0, negative = 1)
embedding_size = model.wv.vectors.shape[1]
print("embedding size--->", embedding_size)
vocab = model.wv.index_to_key

embedding size---> 300


In [41]:
#saves the Word2Vec model

model.save("hing_eng_w2v.model")
print("Model saved!!!")
print('-----------------------')
word_vectors = model.wv
print(word_vectors)
word_vectors.save("word2vec_hing_eng.wordvectors")
#print("Word vectors saved !!!")
#X= list(model.wv.vocab)

Model saved!!!
-----------------------


In [42]:
embeddings_index = Word2Vec.load("hing_eng_w2v.model")
print(embeddings_index)

Word2Vec(vocab=24369, vector_size=300, alpha=0.025)


In [43]:
print(df_labeled.head())
print(len(df_labeled))

                                          tweet_text  is_sarcastic
0  LOL !  BC badaa gaandu hai to ! so jaa lodu ! ...             1
1  @OFFICIAL_FC_PAK apni sakh khud sambhalen aur ...             0
2  Ek aadmi pareshan ho kar Ae bhagwan aisi zinda...             1
3  Lol RT @ThePrachi: @shrikhande Who can sing a ...             1
4  @idrinkblueblood tu ol's kar rahi ho kya? Kya ...             0
91893


In [44]:
#removes mentions, '#', emojis, punctuations, special chars, URLs, words containing numbers, spaces from beginning and end of tweets

def data_preprocessing(source):
    
    source = source.str.lower() #lower case chars
    source = source.str.replace("\w*\d\w*","") #removes all words containing numbers
    #source = source.str.replace("#", "")
    #source = source.str.replace("@", "")
    #source = source.str.replace("@[A-Za-z0-9_]+","")
    source = source.str.replace("[@A-Za-z0-9_]*@[@A-Za-z0-9_]*","")
    #source = source.str.replace("#[A-Za-z0-9_]+","")
    source = source.str.replace("[#A-Za-z0-9_]*#[#A-Za-z0-9_]*","")
    source = source.str.replace("\s+|[!$%&()*+, -./:;<=>?\^_`{|}~]\s*"," ")
    source = source.str.replace("http\S+","")
    
    return source

df_labeled['tweet_text'] = data_preprocessing(df_labeled['tweet_text'])
df_labeled['tweet_text'] = df_labeled['tweet_text'].apply(lambda s: emoji.replace_emoji(s,""))
df_labeled['tweet_text'] = df_labeled['tweet_text'].str.strip()
df_labeled[['tweet_text']].head()

/tmp/ipykernel_3873/3018622983.py:6: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("\w*\d\w*","") #removes all words containing numbers
/tmp/ipykernel_3873/3018622983.py:10: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("[@A-Za-z0-9_]*@[@A-Za-z0-9_]*","")
/tmp/ipykernel_3873/3018622983.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("[#A-Za-z0-9_]*#[#A-Za-z0-9_]*","")
/tmp/ipykernel_3873/3018622983.py:13: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("\s+|[!$%&()*+, -./:;<=>?\^_`{|}~]\s*"," ")
/tmp/ipykernel_3873/3018622983.py:14: FutureWarning: The default value of regex will change from True to False in a future version.
  source = source.str.replace("http\S+","")


tweet_text
0  lol  bc badaa gaandu hai to  so jaa lodu  tere...
1  apni sakh khud sambhalen aur kisi ka saath na ...
2  ek aadmi pareshan ho kar ae bhagwan aisi zinda...
3  lol rt  who can sing a group song alone raavan...
4  tu ol s kar rahi ho kya kya hoga tere kaam sir...

In [45]:
df_labeled.head()

tweet_text  is_sarcastic
0  lol  bc badaa gaandu hai to  so jaa lodu  tere...             1
1  apni sakh khud sambhalen aur kisi ka saath na ...             0
2  ek aadmi pareshan ho kar ae bhagwan aisi zinda...             1
3  lol rt  who can sing a group song alone raavan...             1
4  tu ol s kar rahi ho kya kya hoga tere kaam sir...             0

In [46]:
#finds the unique words in the labeled data

unique_words = set()
df_labeled['tweet_text'].str.lower().str.split().apply(unique_words.update)
unique_words = list(unique_words)
#print(unique_words)
#print('---------------')
print(len(unique_words))

93958


In [47]:
#counts the appearances of the words in the labeled data

results = Counter()
df_labeled['tweet_text'].str.lower().str.split().apply(results.update)
print(results)
#print('-----------------')
#print(type(results))
#print('-----------------')

Counter({'hai': 51160, 'ki': 21224, 'ke': 19471, 'se': 18439, 'ko': 18377, 'to': 17606, 'bhi': 16969, 'ka': 15888, 'nahi': 15425, 'ho': 14862, 'k': 14337, 'hoga': 12832, 'dil': 12760, 'aur': 11643, 'aage': 11483, 'baad': 11214, 'me': 11156, 'hi': 10120, 'na': 9972, 'hain': 9662, 'kya': 9596, 'mazak': 9185, 'kar': 9114, 'lol': 8834, 'ye': 8071, 'koi': 6862, 'mein': 6813, 'kuch': 6542, 'ne': 6458, 'tha': 6395, 'ek': 6339, 'jo': 5997, 'main': 5704, 'aap': 5463, 'bhai': 5382, 'ab': 5193, 'serious': 5193, 'raha': 4966, 'wo': 4696, 'toh': 4684, 'hum': 4598, 'liye': 4391, 'tum': 4304, 'he': 4165, 'par': 4148, 'baat': 4139, 'tu': 4071, 'is': 4069, 'aaj': 4048, 'pe': 4026, 't': 4003, 'h': 3795, 'hota': 3739, 'mere': 3680, 'p': 3633, 'co': 3570, 'nhi': 3528, 'kisi': 3516, 'or': 3499, 'kiya': 3492, 'log': 3454, 'mujhe': 3444, 'http': 3417, 'kabhi': 3328, 'sab': 3240, 'mai': 3234, 'rahe': 3206, 'ha': 3167, 'gaya': 3154, 'yeh': 2979, 'satire': 2903, 'jab': 2864, 'funny': 2766, 'e': 2716, 'ji': 2639

In [48]:
#finds the rare words in the labeled data

rare_words_labeled = []
for item in results:
    if results[item]<10:
       #print(item, results[item])
       rare_words_labeled.append(item)
        
print(rare_words_labeled)  
print('-----------------------')
print(len(rare_words_labeled))
print('-----------------------')

with open("rare_words_labeled.txt", "w") as file:
    file.write(str(rare_words_labeled))

['lodu', 'sakh', 'sambhalen', 'rhne', 'yamdut', 'marate', 'rehete', 'onkine', 'bhokon', 'tauko', 'dukhyo', 'vanera', 'manchhe', 'sadhai', 'dukhirachha', 'vaira', 'saansain', 'adhoori', 'kamiya', 'sunnegey', 'dogey', 'dengey', 'ramrajey', 'osky', 'bohaat', 'kunda', 'liakin', 'aundhi', 'jeh', 'bimmar', 'pawa', 'puchda', 'ethe', 'kudiya', 'hundeh', 'rasmein', 'poorani', 'gathring', 'deten', 'qayanat', 'atharv', 'dogu', 'iwas', 'inoe', 'chood', 'badme', 'baitho', 'doobta', 'pedo', 'wissaley', 'shairr', 'hyn', 'barg', 'bijnesman', 'badlne', 'burkha', 'hahahakar', 'thuuuu', 'vicks', 'baana', 'panama', 'velapanti', 'isee', 'kashmakash', 'lambai', 'chorai', 'relatable', 'chanta', 'chadd', 'gavaani', 'phail', 'chhutkara', 'tweetoo', 'humale', 'manchild', 'crybaby', 'rehab', 'returned', 'aggre', 'ive', 'damaadji', 'khudke', 'shookla', 'physical', 'barobar', 'boltes', 'evda', 'todte', 'hawaldar', 'baataho', 'tuja', 'atiha', 'asliya', 'pasat', 'subtweet', 'chiriya', 'modu', 'hastag', 'marane', 'ph

In [49]:
with open("rare_words_labeled.txt", "r") as file:
    rare_words_labeled = eval(file.readline())

In [50]:
#--->don't run it now
#removes rare words from the labeled data

df_labeled['tweet_text'] = df_labeled['tweet_text'].apply(lambda x: ' '.join([word for word in x.split() if word not in (rare_words_labeled)]))
print(df_labeled.head())

                                          tweet_text  is_sarcastic
0  lol bc badaa gaandu hai to so jaa tere se kuch...             1
1  apni khud aur kisi ka saath na dein yehi log b...             0
2  ek aadmi pareshan ho kar ae bhagwan aisi zinda...             1
3  lol rt who can sing a group song alone raavan ...             1
4  tu ol s kar rahi ho kya kya hoga tere kaam sir...             0


In [51]:
#--->don't run it now
#saves the preprocessed dataframe to a pickle file

print(df_labeled.head())
df_labeled.to_pickle('preprocessed_labeled_hing_eng.pkl')

                                          tweet_text  is_sarcastic
0  lol bc badaa gaandu hai to so jaa tere se kuch...             1
1  apni khud aur kisi ka saath na dein yehi log b...             0
2  ek aadmi pareshan ho kar ae bhagwan aisi zinda...             1
3  lol rt who can sing a group song alone raavan ...             1
4  tu ol s kar rahi ho kya kya hoga tere kaam sir...             0


In [52]:
#loads the preprocessed dataframe from a pickle file

df_labeled = pd.read_pickle('preprocessed_labeled_hing_eng.pkl')
print(df_labeled.head())
print(len(df_labeled))

                                          tweet_text  is_sarcastic
0  lol bc badaa gaandu hai to so jaa tere se kuch...             1
1  apni khud aur kisi ka saath na dein yehi log b...             0
2  ek aadmi pareshan ho kar ae bhagwan aisi zinda...             1
3  lol rt who can sing a group song alone raavan ...             1
4  tu ol s kar rahi ho kya kya hoga tere kaam sir...             0
91893


In [53]:
#finds the unique words in the labeled data after rare words removal

unique_words = set()
df_labeled['tweet_text'].str.lower().str.split().apply(unique_words.update)
unique_words = list(unique_words)
#print(unique_words)
#print('---------------')
print(len(unique_words))

10014


In [54]:
#generates tokenized data for the preprocessed data

#nltk.download('punkt')
df_labeled['tweet_text'] = df_labeled['tweet_text'].apply(nltk.word_tokenize)
df_labeled.head()

tweet_text  is_sarcastic
0  [lol, bc, badaa, gaandu, hai, to, so, jaa, ter...             1
1  [apni, khud, aur, kisi, ka, saath, na, dein, y...             0
2  [ek, aadmi, pareshan, ho, kar, ae, bhagwan, ai...             1
3  [lol, rt, who, can, sing, a, group, song, alon...             1
4  [tu, ol, s, kar, rahi, ho, kya, kya, hoga, ter...             0

In [55]:
#removes all the rows with empty lists

print(len(df_labeled))
df_labeled = df_labeled[df_labeled['tweet_text'].map(lambda d: len(d)) > 0]
print(df_labeled.head(10))
print(len(df_labeled))

91893
                                          tweet_text  is_sarcastic
0  [lol, bc, badaa, gaandu, hai, to, so, jaa, ter...             1
1  [apni, khud, aur, kisi, ka, saath, na, dein, y...             0
2  [ek, aadmi, pareshan, ho, kar, ae, bhagwan, ai...             1
3  [lol, rt, who, can, sing, a, group, song, alon...             1
4  [tu, ol, s, kar, rahi, ho, kya, kya, hoga, ter...             0
5      [yaar, ye, log, tu, serious, ho, gaye, t, co]             0
6  [abey, tumhare, paas, kaam, nahi, hai, jo, twi...             0
7  [ani, jaane, ta, ho, ni, o, hawa, serious, kei...             0
8  [rt, agar, tumne, rt, nahi, kiya, to, mujhse, ...             0
9  [dil, ki, dhadkan, sooni, sooni, bhi, adha, ad...             0
91557


In [56]:
df_labeled.head()

tweet_text  is_sarcastic
0  [lol, bc, badaa, gaandu, hai, to, so, jaa, ter...             1
1  [apni, khud, aur, kisi, ka, saath, na, dein, y...             0
2  [ek, aadmi, pareshan, ho, kar, ae, bhagwan, ai...             1
3  [lol, rt, who, can, sing, a, group, song, alon...             1
4  [tu, ol, s, kar, rahi, ho, kya, kya, hoga, ter...             0

In [57]:
df_hing_eng.head()

tweet_text
194  [singh, dhoni, dd, management, to, release, yu...
200  [seedhe, log, hai, ma, beta, ab, crore, ka, gh...
309  [ab, ham, khade, ho, gaye, hain, ab, ham, aur,...
470                                         [make, up]
571            [cut, marna, koi, umar, se, nahi, haha]

In [58]:
#train test split of labeled data

check_nan = df_labeled['is_sarcastic'].isnull().values.any()
print(check_nan)
check_na = df_labeled['is_sarcastic'].isna().values.any()
print(check_na)
check_nan_ = df_labeled['tweet_text'].isnull().values.any()
print(check_nan_)
check_na_ = df_labeled['tweet_text'].isna().values.any()
print(check_na_)

x_train,x_test,y_train,y_test=train_test_split(df_labeled['tweet_text'], df_labeled['is_sarcastic'], test_size=0.30, random_state=42)
#x_train,x_test,y_train,y_test=train_test_split(padded_tweets, sarcasm_labels, test_size=0.20, random_state=42)
print("x_train_shape--->", x_train.shape)
print("y_train_shape--->", y_train.shape)
print("x_test_shape--->", x_test.shape)
print("y_test_shape--->", y_test.shape)
print(type(x_train))
print("contents of first label--->", y_train[0])

False
False
False
False
x_train_shape---> (64089,)
y_train_shape---> (64089,)
x_test_shape---> (27468,)
y_test_shape---> (27468,)
<class 'pandas.core.series.Series'>
contents of first label---> 1


In [59]:
print(x_train)

42486    [kya, baat, i, ll, say, this, while, the, awar...
81430    [koi, baat, nahi, arjun, yeh, prem, rog, hai, ...
16313    [hum, uss, desh, ke, wasi, hai, jahan, roz, hi...
25490    [indian, parents, ko, badi, badi, baaton, se, ...
69537    [koun, kehta, h, ki, yeh, paise, lete, hain, y...
                               ...                        
6337     [filhal, to, bechare, ko, se, baher, nikal, dy...
56392                                  [boat, http, t, co]
79310    [galti, se, mistake, ho, gaye, lol, ab, kya, k...
868      [to, kese, k, jao, nai, bat, nai, udasi, aage,...
16071                                      [lol, jai, jai]
Name: tweet_text, Length: 64089, dtype: object


In [60]:
print(y_train.value_counts())
print('--------------------------')
print(y_test.value_counts())

0    32461
1    31628
Name: is_sarcastic, dtype: int64
--------------------------
0    13943
1    13525
Name: is_sarcastic, dtype: int64


In [61]:
length = []
for row in x_train:
    #print(row)
    #print(len(row))
    #count = count+1
    #if len(row)>maxi:
    #print(len(row))
    length.append(len(row))
        
#print(length)
print("Max length--->", max(length))
print("Mean length--->", np.mean(length))
print("Standard Deviation of length--->", np.std(length))

#maxi = max(length)
maxi = np.round(np.mean(length) + np.std(length)).astype(int)
print("Maximum length of the sequence--->", maxi)

Max length---> 79
Mean length---> 14.970790619295043
Standard Deviation of length---> 8.82197247942889
Maximum length of the sequence---> 24


In [62]:
total_docs=[]
total_docs.extend(x_train)
total_docs.extend(x_test)
print(total_docs[0:5])

[['kya', 'baat', 'i', 'll', 'say', 'this', 'while', 'the', 'award', 'jab', 'sharafat', 'ke', 'kapde', 'hai', 'tab', 'sabse', 'jyaada', 'maja'], ['koi', 'baat', 'nahi', 'arjun', 'yeh', 'prem', 'rog', 'hai', 'shuru', 'me', 'dukh', 'deta', 'hai', 'aur', 'baad', 'me', 'malik', 'baad', 'me', 'bahut', 'dukh', 'deta', 'hai', 'd'], ['hum', 'uss', 'desh', 'ke', 'wasi', 'hai', 'jahan', 'roz', 'hi', 'panga', 'rehta', 'hai', 'jahan', 'roz', 'roz', 'me', 'ka', 'panga', 'rehta', 'hai', 'iss', 'haal', 'me', 'bhi', 'iss', 'dil', 'me', 'bas', 'ek', 'tiranga', 'rehta', 'hai', 'believe', 'me', 'or', 'die', 'this', 'scene', 'jai', 'hind', 'of', 'india', 't', 'co'], ['indian', 'parents', 'ko', 'badi', 'badi', 'baaton', 'se', 'nahi', 'pe', 'lage', 'se', 'pata', 'chalta', 'hai', 'bache', 'bade', 'ho', 'gaye', 'hai'], ['koun', 'kehta', 'h', 'ki', 'yeh', 'paise', 'lete', 'hain', 'yeh', 'toh', 'bass', 'desh', 'ki', 'karne', 'ke', 'liye', 'bina', 'paise', 'ke', 'kaam', 'kar', 'rhe', 'hain', 'galat', 'toh', 'this

In [63]:
print("tokenizing input data...")
MAX_NB_WORDS = 200000
tokenizer = Tokenizer(num_words=MAX_NB_WORDS, lower=True, char_level=False)
tokenizer.fit_on_texts(total_docs)
#tokenizer.fit_on_texts(x_train)
word_seq_train = tokenizer.texts_to_sequences(x_train)
word_seq_test = tokenizer.texts_to_sequences(x_test)
word_index = tokenizer.word_index

tokenizing input data...


In [64]:
print(len(word_seq_train))
print(word_seq_train[0])
print(len(word_seq_test))
print(word_seq_test[0])
print("dictionary size: ", len(word_index))

64089
[21, 46, 109, 3592, 183, 334, 4561, 102, 2103, 72, 6955, 3, 4209, 1, 253, 394, 3425, 2024]
27468
[94, 604, 131, 21, 12, 63, 51, 56]
dictionary size:  10013


In [65]:
#pads to the length of the longest sequence

word_seq_train = pad_sequences(word_seq_train, maxlen=maxi, padding='post')
word_seq_test = pad_sequences(word_seq_test, maxlen=maxi, padding='post')
print(word_seq_train[0])
print(word_seq_train.shape)
print(word_seq_test.shape)

[  21   46  109 3592  183  334 4561  102 2103   72 6955    3 4209    1
  253  394 3425 2024    0    0    0    0    0    0]
(64089, 24)
(27468, 24)


In [66]:
#builds the embedding matrix

print('preparing embedding matrix...')
embed_dim = embedding_size
words_not_found = []
nb_words = min(MAX_NB_WORDS, len(word_index))
embedding_matrix = np.random.rand(nb_words+1, embed_dim)

for word, i in word_index.items():
    if i >= nb_words:
        continue
    #print(word)

    if embeddings_index.wv.__contains__(word): 

        embedding_vector = embeddings_index.wv[word]
    
        embedding_matrix[i] = embedding_vector
    else:
        words_not_found.append(word)
#print(embedding_matrix)
print('number of null word embeddings: %d' % np.sum(np.sum(embedding_matrix, axis=1) == 0))
print(embedding_matrix.shape)
print(len(embedding_matrix[34]))

preparing embedding matrix...
number of null word embeddings: 0
(10014, 300)
300


In [67]:
print(words_not_found)

['satire', 'mock', 'taunt', 'joking', 'mocks', 'drill', 'shuruvaat', 'uraya', 'doraniya', 'teetar', 'sarafa', 'aneh', 'muddaton', 'jeejee', 'rakt', 'mehkta', 'marsha', 'mazahiya', 'yuup', 'uratay', 'urana', 'barhne', 'tazeem', 'khushki', 'rakht', 'shaiqeen', 'hamrah', 'muqarara', 'baqaya', 'badhna', 'kunwari', 'badna', 'moch', 'yadda', 'urao', 'ogra', 'urate', 'badega', 'meedha', 'hadippa', 'meeda', 'badhiye', 'zindgaani', 'mudaton', 'atfaal', 'ves', 'aankhoun', 'maatram', 'haso', 'wena', 'meehun', 'picche', 'maury', 'uraty', 'uraa', 'taane', 'putt', 'heey', 'nalla', 'badane', 'uranay', 'anqareb', 'khatama', 'haneko', 'mesage', 'daish', 'safarshat', 'lahra', 'varah', 'hazm', 'adore', 'ikr', 'urata', 'taqsim', 'janaabe', 'natmastak', 'apnajoy', 'prank', 'uffffff', 'cie', 'uu', 'rw', 'rotiya', 'jalanay', 'sarcastic', 'soochit', 'udaye', 'gharibon', 'vyang', 'wasail', 'zendeh', 'unh', 'tahe', 'dafnaane', 'minnatein', 'kaaliya', 'mulgi', 'apathy', 'chalke', 'daay', 'badhegi', 'jumbish', 'e

In [68]:
#words not found in the embeddings

print("sample words not found: ", np.random.choice(words_not_found, 10))

sample words not found:  ['nalla' 'addat' 'maheenay' 'arsey' 'bhagoge' 'zip' 'unglion' 'bharai'
 'sujh' 'cie']


In [69]:
#define callbacks
early_stopping = EarlyStopping(monitor='val_loss', min_delta=0.01, patience=4, verbose=1)
callbacks_list = [early_stopping]

In [70]:
#Attention BiLSTM

from keras import backend as K
#from keras.engine.topology import Layer
from tensorflow.keras.layers import Layer
from keras import initializers, regularizers, constraints


class Attention(Layer):
    def __init__(self, step_dim,
                 W_regularizer=None, b_regularizer=None,
                 W_constraint=None, b_constraint=None,
                 bias=True, **kwargs):
        self.supports_masking = True
        self.init = initializers.get('glorot_uniform')

        self.W_regularizer = regularizers.get(W_regularizer)
        self.b_regularizer = regularizers.get(b_regularizer)

        self.W_constraint = constraints.get(W_constraint)
        self.b_constraint = constraints.get(b_constraint)

        self.bias = bias
        self.step_dim = step_dim
        self.features_dim = 0
        super(Attention, self).__init__(**kwargs)

    def build(self, input_shape):
        assert len(input_shape) == 3

        self.W = self.add_weight( shape=(input_shape[-1],),
                                 initializer=self.init,
                                 name='{}_W'.format(self.name),
                                 regularizer=self.W_regularizer,
                                 constraint=self.W_constraint)
        self.features_dim = input_shape[-1]
        #print(self.name)
        if self.bias:
            self.b = self.add_weight(shape=(input_shape[1],),
                                     initializer='zero',
                                     name='{}_b'.format(self.name),
                                     regularizer=self.b_regularizer,
                                     constraint=self.b_constraint)
        else:
            self.b = None

        self.built = True

    def compute_mask(self, input, input_mask=None):
        return None

    def call(self, x, mask=None):
        features_dim = self.features_dim
        step_dim = self.step_dim

        eij = K.reshape(K.dot(K.reshape(x, (-1, features_dim)),
                        K.reshape(self.W, (features_dim, 1))), (-1, step_dim))

        if self.bias:
            eij += self.b

        eij = K.tanh(eij)

        a = K.exp(eij)

        if mask is not None:
            a *= K.cast(mask, K.floatx())

        a /= K.cast(K.sum(a, axis=1, keepdims=True) + K.epsilon(), K.floatx())

        a = K.expand_dims(a)
        weighted_input = x * a
        return K.sum(weighted_input, axis=1)

    def compute_output_shape(self, input_shape):
        return input_shape[0],  self.features_dim


In [73]:
lstm_out1 = 150
#bilstm_out1 = 96
#lstm_out2 = 32
#dropout = 0.2
#recurrent_dropout = 0.2

inp = Input(shape=(maxi, ))
x = Embedding(nb_words+1, embed_dim, weights=[embedding_matrix], trainable=False)(inp)
x = Bidirectional(LSTM(lstm_out1, return_sequences=True, dropout=0.20, recurrent_dropout=0.20))(x)
x = Attention(maxi)(x)
x = Dense(256, activation="relu")(x)
#x = Dropout(0.25)(x)
x = Dense(1, activation="sigmoid")(x)
model = Model(inputs=inp, outputs=x)

adam = Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
model.compile(loss='binary_crossentropy',optimizer='adam', metrics=['accuracy'])
model.summary()

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 24)]              0         
                                                                 
 embedding_1 (Embedding)     (None, 24, 300)           3004200   
                                                                 
 bidirectional_1 (Bidirectio  (None, 24, 300)          541200    
 nal)                                                            
                                                                 
 attention_1 (Attention)     (None, 300)               324       
                                                                 
 dense_2 (Dense)             (None, 256)               77056     
                                                                 
 dense_3 (Dense)             (None, 1)                 257       
                                                           

In [74]:
#trains attention BiLSTM model 

model.fit(word_seq_train, y_train, batch_size=64, epochs=20, validation_split=0.1, shuffle=True, callbacks = callbacks_list)
#model.save('att_bilstm.h5') 

Epoch 1/20
902/902 [==============================] - 258s 277ms/step - loss: 0.2905 - accuracy: 0.8871 - val_loss: 0.2011 - val_accuracy: 0.9293
Epoch 2/20
902/902 [==============================] - 349s 387ms/step - loss: 0.1770 - accuracy: 0.9414 - val_loss: 0.1503 - val_accuracy: 0.9537
Epoch 3/20
902/902 [==============================] - 237s 262ms/step - loss: 0.1348 - accuracy: 0.9569 - val_loss: 0.1342 - val_accuracy: 0.9579
Epoch 4/20
902/902 [==============================] - 232s 257ms/step - loss: 0.1175 - accuracy: 0.9615 - val_loss: 0.1348 - val_accuracy: 0.9576
Epoch 5/20
902/902 [==============================] - 232s 257ms/step - loss: 0.1037 - accuracy: 0.9660 - val_loss: 0.1309 - val_accuracy: 0.9563
Epoch 6/20
902/902 [==============================] - 231s 256ms/step - loss: 0.0896 - accuracy: 0.9696 - val_loss: 0.1422 - val_accuracy: 0.9557
Epoch 7/20
902/902 [==============================] - 238s 264ms/step - loss: 0.0778 - accuracy: 0.9729 - val_loss: 0.1434 -

In [75]:
#model = load_model('att_bilstm.h5')
y_pred_proba = model.predict(word_seq_test)
#print(y_pred_proba)
#print('---------------')

y_pred_class = np.round(y_pred_proba)
y_pred_class = y_pred_class.squeeze() #makes y_pred_class 1 dim
'''print(y_pred_class)
print(type(y_pred_class))
print(len(y_pred_class))
print(len(y_test))
print('---------------')'''

acc = accuracy_score(y_test, y_pred_class) * 100
print("Accuracy is--->", acc)

859/859 [==============================] - 67s 77ms/step
Accuracy is---> 95.78418523372652


In [78]:
#this one--->LSTM

lstm_out1 = 150
'''bilstm_out1 = 96
lstm_out2 = 32
dropout = 0.2
recurrent_dropout = 0.2'''

model = Sequential()
model.add(Embedding(nb_words+1, embed_dim, weights=[embedding_matrix], input_length=maxi, trainable=False))
model.add(LSTM(lstm_out1, dropout=0.2, recurrent_dropout=0.2))

model.add(Dense(64, activation='relu'))

model.add(Dense(1, activation='sigmoid'))

adam = Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)

model.compile(loss='binary_crossentropy',
                  optimizer=adam,
                  metrics=['accuracy'])

model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_2 (Embedding)     (None, 24, 300)           3004200   
                                                                 
 lstm_2 (LSTM)               (None, 150)               270600    
                                                                 
 dense_4 (Dense)             (None, 64)                9664      
                                                                 
 dense_5 (Dense)             (None, 1)                 65        
                                                                 
Total params: 3,284,529
Trainable params: 280,329
Non-trainable params: 3,004,200
_________________________________________________________________


/home/user/anaconda3/lib/python3.9/site-packages/keras/optimizers/optimizer_v2/adam.py:110: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


In [79]:
#trains the LSTM model

model.fit(word_seq_train, y_train, batch_size=64, epochs=20, validation_split=0.1, shuffle=True, callbacks = callbacks_list)
model.save('lstm.h5') 

Epoch 1/20
902/902 [==============================] - 156s 168ms/step - loss: 0.3422 - accuracy: 0.8571 - val_loss: 0.2401 - val_accuracy: 0.9134
Epoch 2/20
902/902 [==============================] - 196s 217ms/step - loss: 0.2348 - accuracy: 0.9121 - val_loss: 0.2166 - val_accuracy: 0.9186
Epoch 3/20
902/902 [==============================] - 145s 160ms/step - loss: 0.1967 - accuracy: 0.9285 - val_loss: 0.1795 - val_accuracy: 0.9334
Epoch 4/20
902/902 [==============================] - 174s 193ms/step - loss: 0.1636 - accuracy: 0.9427 - val_loss: 0.1602 - val_accuracy: 0.9423
Epoch 5/20
902/902 [==============================] - 141s 156ms/step - loss: 0.1373 - accuracy: 0.9529 - val_loss: 0.1470 - val_accuracy: 0.9521
Epoch 6/20
902/902 [==============================] - 147s 163ms/step - loss: 0.1196 - accuracy: 0.9600 - val_loss: 0.1422 - val_accuracy: 0.9554
Epoch 7/20
902/902 [==============================] - 159s 176ms/step - loss: 0.1082 - accuracy: 0.9635 - val_loss: 0.1439 -

In [80]:
#model = load_model('att_bilstm.h5')
y_pred_proba = model.predict(word_seq_test)
#print(y_pred_proba)
#print('---------------')

y_pred_class = np.round(y_pred_proba)
y_pred_class = y_pred_class.squeeze() #makes y_pred_class 1 dim
'''print(y_pred_class)
print(type(y_pred_class))
print(len(y_pred_class))
print(len(y_test))
print('---------------')'''

acc = accuracy_score(y_test, y_pred_class) * 100
print("Accuracy is--->", acc)

859/859 [==============================] - 22s 25ms/step
Accuracy is---> 95.2271734381826


In [81]:
# BiLSTM

lstm_out1 = 150
bilstm_out1 = 96
lstm_out2 = 32
dropout = 0.2
recurrent_dropout = 0.2

# main model
inputt = Input(shape=(maxi,))
model = Embedding(nb_words+1, embed_dim, weights=[embedding_matrix],input_length=maxi,trainable = False)(inputt)
model =  Bidirectional (LSTM (lstm_out1, return_sequences=True, dropout=0.2, recurrent_dropout=0.2), merge_mode='concat')(model)
model = TimeDistributed(Dense(10,activation='relu'))(model)
model = Flatten()(model)
model = Dense(64,activation='relu')(model)
output = Dense(1,activation='sigmoid')(model)
model = Model(inputt,output)
adam = Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
model.compile(loss='binary_crossentropy',optimizer='adam', metrics=['accuracy'])
model.summary()

Model: "model_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_3 (InputLayer)        [(None, 24)]              0         
                                                                 
 embedding_3 (Embedding)     (None, 24, 300)           3004200   
                                                                 
 bidirectional_2 (Bidirectio  (None, 24, 300)          541200    
 nal)                                                            
                                                                 
 time_distributed (TimeDistr  (None, 24, 10)           3010      
 ibuted)                                                         
                                                                 
 flatten (Flatten)           (None, 240)               0         
                                                                 
 dense_7 (Dense)             (None, 64)                1542

/home/user/anaconda3/lib/python3.9/site-packages/keras/optimizers/optimizer_v2/adam.py:110: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


In [82]:
model.fit(word_seq_train, y_train, batch_size=64, epochs=20, validation_split=0.1, shuffle=True, callbacks = callbacks_list)
model.save('bilstm.h5') 

Epoch 1/20
902/902 [==============================] - 340s 367ms/step - loss: 0.3139 - accuracy: 0.8727 - val_loss: 0.2118 - val_accuracy: 0.9256
Epoch 2/20
902/902 [==============================] - 297s 330ms/step - loss: 0.1883 - accuracy: 0.9369 - val_loss: 0.1656 - val_accuracy: 0.9455
Epoch 3/20
902/902 [==============================] - 264s 293ms/step - loss: 0.1406 - accuracy: 0.9555 - val_loss: 0.1419 - val_accuracy: 0.9549
Epoch 4/20
902/902 [==============================] - 257s 285ms/step - loss: 0.1200 - accuracy: 0.9611 - val_loss: 0.1364 - val_accuracy: 0.9580
Epoch 5/20
902/902 [==============================] - 241s 267ms/step - loss: 0.1034 - accuracy: 0.9662 - val_loss: 0.1358 - val_accuracy: 0.9579
Epoch 6/20
902/902 [==============================] - 240s 266ms/step - loss: 0.0899 - accuracy: 0.9691 - val_loss: 0.1405 - val_accuracy: 0.9560
Epoch 7/20
902/902 [==============================] - 231s 256ms/step - loss: 0.0779 - accuracy: 0.9734 - val_loss: 0.1476 -

In [83]:
#model = load_model('att_bilstm.h5')
y_pred_proba = model.predict(word_seq_test)
#print(y_pred_proba)
#print('---------------')

y_pred_class = np.round(y_pred_proba)
y_pred_class = y_pred_class.squeeze() #makes y_pred_class 1 dim
'''print(y_pred_class)
print(type(y_pred_class))
print(len(y_pred_class))
print(len(y_test))
print('---------------')'''

acc = accuracy_score(y_test, y_pred_class) * 100
print("Accuracy is--->", acc)

859/859 [==============================] - 48s 55ms/step
Accuracy is---> 95.48929663608563


In [89]:
#CNN1

#model parameters

num_kernels=200
stride=1
embed_dim = 300
weight_decay = 1e-4

#parallel layers 
kernel_size=7
kernel_size_p1=3
kernel_size_p2=6
kernel_size_p3=9
kernel_size_p4=12

#CNN architecture
print("training CNN ...")
model = Sequential()
model.add(Embedding(nb_words+1, embed_dim, weights=[embedding_matrix], input_length=maxi, trainable=False))
model.add(Conv1D(num_kernels, kernel_size, activation='relu', padding='same'))
model.add(MaxPooling1D(2))
model.add(Conv1D(num_kernels, kernel_size, activation='relu', padding='same'))
#model.add(GlobalMaxPooling1D())
model.add(MaxPooling1D(2))
#model.add(Dense(64, activation='relu', kernel_regularizer=regularizers.l2(weight_decay)))
model.add(GlobalMaxPooling1D())
model.add(Dropout(0.5))
model.add(Dense(128, activation='relu'))
model.add(Dense(64, activation='relu'))
#model.add(Dense(num_classes, activation='sigmoid'))  #multi-label (k-hot encoding)
model.add(Dense(1, activation='sigmoid')) 

adam = Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

training CNN ...
Model: "sequential_6"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_6 (Embedding)     (None, 24, 300)           3004200   
                                                                 
 conv1d_4 (Conv1D)           (None, 24, 200)           420200    
                                                                 
 max_pooling1d_4 (MaxPooling  (None, 12, 200)          0         
 1D)                                                             
                                                                 
 conv1d_5 (Conv1D)           (None, 12, 200)           280200    
                                                                 
 max_pooling1d_5 (MaxPooling  (None, 6, 200)           0         
 1D)                                                             
                                                                 
 global_max_pooling1d_2 (Glo  (None, 

/home/user/anaconda3/lib/python3.9/site-packages/keras/optimizers/optimizer_v2/adam.py:110: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


In [90]:
model.fit(word_seq_train, y_train, batch_size=64, epochs=20, validation_split=0.1, shuffle=True, callbacks = callbacks_list)
model.save('cnn1.h5') 

Epoch 1/20
902/902 [==============================] - 144s 158ms/step - loss: 0.3950 - accuracy: 0.8257 - val_loss: 0.2944 - val_accuracy: 0.8861
Epoch 2/20
902/902 [==============================] - 145s 161ms/step - loss: 0.2662 - accuracy: 0.8998 - val_loss: 0.2456 - val_accuracy: 0.9126
Epoch 3/20
902/902 [==============================] - 123s 136ms/step - loss: 0.2247 - accuracy: 0.9165 - val_loss: 0.2481 - val_accuracy: 0.9128
Epoch 4/20
902/902 [==============================] - 167s 185ms/step - loss: 0.1978 - accuracy: 0.9271 - val_loss: 0.2398 - val_accuracy: 0.9143
Epoch 5/20
902/902 [==============================] - 125s 139ms/step - loss: 0.1729 - accuracy: 0.9375 - val_loss: 0.2349 - val_accuracy: 0.9167
Epoch 6/20
902/902 [==============================] - 111s 123ms/step - loss: 0.1500 - accuracy: 0.9455 - val_loss: 0.2617 - val_accuracy: 0.9081
Epoch 7/20
902/902 [==============================] - 111s 124ms/step - loss: 0.1297 - accuracy: 0.9531 - val_loss: 0.2620 -

In [91]:
#model = load_model('att_bilstm.h5')
y_pred_proba = model.predict(word_seq_test)
#print(y_pred_proba)
#print('---------------')

y_pred_class = np.round(y_pred_proba)
y_pred_class = y_pred_class.squeeze() #makes y_pred_class 1 dim
'''print(y_pred_class)
print(type(y_pred_class))
print(len(y_pred_class))
print(len(y_test))
print('---------------')'''

acc = accuracy_score(y_test, y_pred_class) * 100
print("Accuracy is--->", acc)

859/859 [==============================] - 26s 30ms/step
Accuracy is---> 90.12669287898646


In [93]:
#CNN2

#num_classes = len(label_names)
num_classes = 2

inputt = Input(shape=(maxi,))
model = Embedding(nb_words+1, embed_dim, weights=[embedding_matrix],input_length=maxi,trainable = False)(inputt)
tower_1 = Conv1D(num_kernels, kernel_size_p1, padding='same', activation='relu', strides=stride)(model)
tower_2 = Conv1D(num_kernels, kernel_size_p2, padding='same', activation='relu', strides=stride)(model)
tower_3 = Conv1D(num_kernels, kernel_size_p3, padding='same', activation='relu', strides=stride)(model)
tower_4 = Conv1D(num_kernels, kernel_size_p4, padding='same', activation='relu', strides=stride)(model)
model = keras.layers.concatenate([tower_1, tower_2, tower_3, tower_4], axis=1)
model = GlobalMaxPooling1D()(model)
model = Dropout(0.5)(model)
#model = Flatten()(model)
model = Dense(128, activation='relu')(model)
model = Dense(64, activation='relu')(model)
#output = Dense(num_classes, activation='sigmoid')(model)
output = Dense(1, activation='sigmoid')(model)
model = Model(inputt, output)

#adam = optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
model.summary()

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_5 (InputLayer)           [(None, 24)]         0           []                               
                                                                                                  
 embedding_7 (Embedding)        (None, 24, 300)      3004200     ['input_5[0][0]']                
                                                                                                  
 conv1d_6 (Conv1D)              (None, 24, 200)      180200      ['embedding_7[0][0]']            
                                                                                                  
 conv1d_7 (Conv1D)              (None, 24, 200)      360200      ['embedding_7[0][0]']            
                                                                                            

In [94]:
model.fit(word_seq_train, y_train, batch_size=64, epochs=20, validation_split=0.1, shuffle=True, callbacks = callbacks_list)
model.save('cnn2.h5') 

Epoch 1/20
902/902 [==============================] - 235s 259ms/step - loss: 0.4441 - accuracy: 0.7914 - val_loss: 0.3115 - val_accuracy: 0.8733
Epoch 2/20
902/902 [==============================] - 296s 328ms/step - loss: 0.3107 - accuracy: 0.8776 - val_loss: 0.2447 - val_accuracy: 0.9084
Epoch 3/20
902/902 [==============================] - 311s 345ms/step - loss: 0.2650 - accuracy: 0.8999 - val_loss: 0.2289 - val_accuracy: 0.9156
Epoch 4/20
902/902 [==============================] - 279s 309ms/step - loss: 0.2455 - accuracy: 0.9071 - val_loss: 0.2260 - val_accuracy: 0.9193
Epoch 5/20
902/902 [==============================] - 240s 266ms/step - loss: 0.2248 - accuracy: 0.9155 - val_loss: 0.2241 - val_accuracy: 0.9165
Epoch 6/20
902/902 [==============================] - 254s 282ms/step - loss: 0.2061 - accuracy: 0.9231 - val_loss: 0.2193 - val_accuracy: 0.9156
Epoch 7/20
902/902 [==============================] - 232s 257ms/step - loss: 0.1897 - accuracy: 0.9290 - val_loss: 0.2323 -

In [95]:
#model = load_model('att_bilstm.h5')
y_pred_proba = model.predict(word_seq_test)
#print(y_pred_proba)
#print('---------------')

y_pred_class = np.round(y_pred_proba)
y_pred_class = y_pred_class.squeeze() #makes y_pred_class 1 dim
'''print(y_pred_class)
print(type(y_pred_class))
print(len(y_pred_class))
print(len(y_test))
print('---------------')'''

acc = accuracy_score(y_test, y_pred_class) * 100
print("Accuracy is--->", acc)

859/859 [==============================] - 56s 64ms/step
Accuracy is---> 90.80748507354012
